In [1]:
from data_generator.csv_data_processor import CSVDataProcessor
from utils.util_funcs import get_row_count, display_df
from utils.read_write import read_postgres_table
from spark_instance import spark
from pyspark.sql.functions import col, datediff, current_date, lower, lit, rand, array, floor, concat, when, row_number, expr
  

/Users/jacobbickerstaff/Desktop/Development/health-data-etl-kaggle/venv/lib/python3.11/site-packages/pyspark/pandas/__init__.py:50: UserWarning: 'PYARROW_IGNORE_TIMEZONE' environment variable was not set. It is required to set this environment variable to '1' in both driver and executor sides if you use pyarrow>=2.0.0. pandas-on-Spark will set it for you but it does not work if there is a Spark context already launched.
  warnings.warn(
24/02/06 22:24:59 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


In [2]:
# csv_reader = CSVDataProcessor(spark, "data/healthcare_dataset.csv")
# 
# # Read the CSV file
# raw_df = csv_reader.run()


In [3]:
# min_age_days = 1 * 365  # Minimum age in days (18 years)
# max_age_days = 90 * 365  # Maximum age in days (90 years)
# 
# raw_df = (raw_df.withColumn("DOB", expr(f"date_sub(current_date(), CAST(round(rand() * ({max_age_days} - {min_age_days}) + {min_age_days}) AS INT))"))
#         .withColumn("Age", floor(datediff(current_date(), col("DOB")) / 365.25)))




In [23]:
df = read_postgres_table("dob_age_raw_data")

In [24]:
df.show()

+--------------------+---+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+
|                name|Age|gender|blood_type|medical_condition|date_of_admission|            doctor|            hospital|insurance_provider|    billing_amount|room_number|admission_type|discharge_date| medication|test_results|       DOB|
+--------------------+---+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+
|     Tiffany Ramirez| 39|Female|        O-|         Diabetes|       2022-11-17|    Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|        146|      Elective|    2022-12-01|    Aspirin|Inconclusive|1984-09-30|
|         Ruben Burns| 16|  Male|        O+|        

In [25]:
df.where(col("Age") < 16).show()

+------------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+
|              name|Age|gender|blood_type|medical_condition|date_of_admission|          doctor|            hospital|insurance_provider|    billing_amount|room_number|admission_type|discharge_date| medication|test_results|       DOB|
+------------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+--------------+-----------+------------+----------+
|        Ryan Hayes| 14|  Male|        A+|         Diabetes|       2020-12-17|    Kristin Dunn|Smith, Edwards an...|             Aetna| 24903.03726973869|        215|      Elective|    2020-12-22|    Aspirin|    Abnormal|2009-02-26|
|    Steven Bennett|  5|  Male|        O-|           Asthma|       2

In [26]:
from constants.admission_types_tests_dataset import admission_mapping, admission_tests
# Flatten the mapping and create a DataFrame
flattened = [
    (top_level, sub_level, stay_type, admission_tests.get(sub_level, ["No tests"]))
    for top_level, sub_level_dict in admission_mapping.items()
    for sub_level, stay_types in sub_level_dict.items()
    for stay_type in stay_types
]



In [27]:
mapping_df = spark.createDataFrame(flattened, ["top_level_admission", "sub_level_admission", "stay_type", "possible_tests"])

display_df(mapping_df)

top_level_admission      sub_level_admission    stay_type  \
0            emergency               injury_rtc  day_patient   
1            emergency               injury_rtc    inpatient   
2            emergency           self_inflicted    inpatient   
3            emergency               cardiology  day_patient   
4            emergency               cardiology    inpatient   
5            emergency                neurology    inpatient   
6            emergency              pulmonology  day_patient   
7            emergency              pulmonology    inpatient   
8            emergency      infectious_diseases   outpatient   
9            emergency      infectious_diseases    inpatient   
10         gp_referral                   mental   outpatient   
11         gp_referral                   mental    inpatient   
12         gp_referral              orthopedics  day_patient   
13         gp_referral              orthopedics    inpatient   
14         gp_referral         gastroenterology   outpatient   
15         gp_referral         gastroenterology  day_patient   
16         gp_referral            endocrinology   outpatient   
17         gp_referral              dermatology   outpatient   
18         gp_referral               geriatrics   outpatient   
19         gp_referral               geriatrics    inpatient   
20   hospital_referral                   cancer  day_patient   
21   hospital_referral                   cancer    inpatient   
22   hospital_referral               nephrology    inpatient   
23   hospital_referral               cardiology  day_patient   
24   hospital_referral               cardiology    inpatient   
25   hospital_referral                neurology    inpatient   
26   hospital_referral                 oncology  day_patient   
27   hospital_referral                 oncology    inpatient   
28   hospital_referral  otorhinolaryngology_ENT  day_patient   
29   hospital_referral  otorhinolaryngology_ENT    inpatient   
30       self_referral                   mental   outpatient   
31       self_referral              dermatology   outpatient   
32       self_referral              orthopedics  day_patient   
33       self_referral         gastroenterology   outpatient   
34       self_referral            endocrinology   outpatient   
35       self_referral                 oncology   outpatient   
36       self_referral                 oncology  day_patient   
37       self_referral                 oncology    inpatient   
38            elective                maternity  day_patient   
39            elective                maternity    inpatient   
40            elective              orthopedics  day_patient   
41            elective              orthopedics    inpatient   
42            elective               obstetrics    inpatient   
43            elective            ophthalmology  day_patient   
44            elective            ophthalmology   outpatient   
45            elective               geriatrics   outpatient   
46            elective               geriatrics    inpatient   

                                       possible_tests  
0    [X-rays, CT scans, MRI, Ultrasound, Blood tests]  
1    [X-rays, CT scans, MRI, Ultrasound, Blood tests]  
2   [Psychological assessment, X-rays (for physica...  
3   [ECG, Echocardiogram, Stress tests, Cardiac ca...  
4   [ECG, Echocardiogram, Stress tests, Cardiac ca...  
5   [MRI or CT scans of the brain, Electroencephal...  
6   [Pulmonary function tests, Chest X-ray, CT sca...  
7   [Pulmonary function tests, Chest X-ray, CT sca...  
8   [Blood cultures, PCR tests, Antibody tests, Im...  
9   [Blood cultures, PCR tests, Antibody tests, Im...  
10  [Psychological evaluation, Blood tests, Brain ...  
11  [Psychological evaluation, Blood tests, Brain ...  
12   [X-rays, MRI, CT scans, Bone scans, Blood tests]  
13   [X-rays, MRI, CT scans, Bone scans, Blood tests]  
14  [Endoscopy, Colonoscopy, Blood tests, Stool te...  
15  [Endoscopy, Colonoscopy, Blood

In [28]:
# create joining column to mapping_df
admission_types = list(admission_mapping.keys())

print(admission_types)

keys_array = array([lit(key) for key in admission_types])


df = df.withColumn("top_level_admission", keys_array[floor(rand() * len(admission_types))]).drop("admission_type")


['emergency', 'gp_referral', 'hospital_referral', 'self_referral', 'elective']


In [29]:
df.show()

+--------------------+---+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+-------------------+
|                name|Age|gender|blood_type|medical_condition|date_of_admission|            doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|       DOB|top_level_admission|
+--------------------+---+------+----------+-----------------+-----------------+------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+-------------------+
|     Tiffany Ramirez| 39|Female|        O-|         Diabetes|       2022-11-17|    Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|        146|    2022-12-01|    Aspirin|Inconclusive|1984-09-30|           elective|
|         Ruben Burns| 16|  Male

In [30]:

# Define constants and conditions
female_only = ['maternity', 'obstetrics']
is_female = lower(col('gender')) == 'female'
is_pediatric = col("Age") < 18
is_geriatric = (col("Age") >= 65) & (col("sub_level_admission") == "geriatrics")

In [31]:
from data_generator.constants import ColConstants

df = (df.withColumn("is_female", is_female)
        .withColumn("is_pediatric", is_pediatric)
      )

In [32]:
df.show(n=9999)

+--------------------+---+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+-------------------+---------+------------+
|                name|Age|gender|blood_type|medical_condition|date_of_admission|              doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|       DOB|top_level_admission|is_female|is_pediatric|
+--------------------+---+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+-------------------+---------+------------+
|     Tiffany Ramirez| 39|Female|        O-|         Diabetes|       2022-11-17|      Patrick Parker|    Wallace-Hamilton|          Medicare| 37490.98336352819|        146|    2022-12-01|    Aspirin|

In [33]:
mapping_df.show()

+-------------------+-------------------+-----------+--------------------+
|top_level_admission|sub_level_admission|  stay_type|      possible_tests|
+-------------------+-------------------+-----------+--------------------+
|          emergency|         injury_rtc|day_patient|[X-rays, CT scans...|
|          emergency|         injury_rtc|  inpatient|[X-rays, CT scans...|
|          emergency|     self_inflicted|  inpatient|[Psychological as...|
|          emergency|         cardiology|day_patient|[ECG, Echocardiog...|
|          emergency|         cardiology|  inpatient|[ECG, Echocardiog...|
|          emergency|          neurology|  inpatient|[MRI or CT scans ...|
|          emergency|        pulmonology|day_patient|[Pulmonary functi...|
|          emergency|        pulmonology|  inpatient|[Pulmonary functi...|
|          emergency|infectious_diseases| outpatient|[Blood cultures, ...|
|          emergency|infectious_diseases|  inpatient|[Blood cultures, ...|
|        gp_referral|    

In [34]:
df = df.join(mapping_df, "top_level_admission", "inner")

In [35]:
df.show(n=990)

+-------------------+--------------------+---+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+---------+------------+-------------------+-----------+--------------------+
|top_level_admission|                name|Age|gender|blood_type|medical_condition|date_of_admission|              doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|       DOB|is_female|is_pediatric|sub_level_admission|  stay_type|      possible_tests|
+-------------------+--------------------+---+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+---------+------------+-------------------+-----------+--------------------+
|           elective|     Tiffany Ramire

In [40]:
df.select("name", "sub_level_admission", "top_level_admission", "stay_type", "is_pediatric", "Age", "DOB").orderBy("name", "sub_level_admission").where(col("name")=="Aaron Patel").show(n=200)

+-----------+-------------------+-------------------+-----------+------------+---+----------+
|       name|sub_level_admission|top_level_admission|  stay_type|is_pediatric|Age|       DOB|
+-----------+-------------------+-------------------+-----------+------------+---+----------+
|Aaron Patel|        dermatology|      self_referral|out_patient|       false| 54|1969-09-23|
|Aaron Patel|        dermatology|      self_referral|out_patient|       false| 88|1935-08-05|
|Aaron Patel|      endocrinology|      self_referral|out_patient|       false| 54|1969-09-23|
|Aaron Patel|      endocrinology|      self_referral|out_patient|       false| 88|1935-08-05|
|Aaron Patel|   gastroenterology|      self_referral|out_patient|       false| 54|1969-09-23|
|Aaron Patel|   gastroenterology|      self_referral|out_patient|       false| 88|1935-08-05|
|Aaron Patel|             mental|      self_referral|out_patient|       false| 54|1969-09-23|
|Aaron Patel|             mental|      self_referral|out_pat

In [37]:
from pyspark.sql import Window

from pyspark.sql.functions import when, col, lit, concat

df = (df.withColumn("stay_type", 
                   when(col("stay_type") == "day_patient", lit("out_patient"))
                   .when(col("stay_type") == "outpatient", lit("out_patient"))
                   .otherwise(col("stay_type"))) 
       .withColumn('stay_name', 
                   when(col('stay_type') == 'out_patient', concat(col('name'), lit('_out_patient')))
                   .otherwise(when(col('stay_type') == 'inpatient', concat(col('name'), lit('_inpatient')))
                   .otherwise(col('name')))))




In [39]:
df.where((col("sub_level_admission") == "injury_rtc")).show()

+-------------------+--------------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+---------+------------+-------------------+-----------+--------------------+--------------------+
|top_level_admission|                name|Age|gender|blood_type|medical_condition|date_of_admission|          doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|       DOB|is_female|is_pediatric|sub_level_admission|  stay_type|      possible_tests|           stay_name|
+-------------------+--------------------+---+------+----------+-----------------+-----------------+----------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+---------+------------+-------------------+-----------+--------------------+-----------

In [41]:
# Define a window specification that partitions data by 'top_level_admission' (or another unique patient identifier if needed)
windowSpec = Window.partitionBy('name', 'stay_name').orderBy(rand())

# Assign row numbers within each partition in a random order
ranked_df = df.withColumn("is_geriatric", is_geriatric).withColumn("row_num", row_number().over(windowSpec))


In [47]:
ranked_df.orderBy("name", "sub_level_admission").where((col("sub_level_admission") == "injury_rtc") & (col('name') == 'Aaron Patel')).show(n=200)

+-------------------+-----------+------+----------+-----------------+-----------------+--------------+-------------+------------------+------------------+-----------+--------------+----------+------------+----------+----------+---+---------+------------+-------------------+-----------+--------------------+--------------------+------------+-------+
|top_level_admission|       name|gender|blood_type|medical_condition|date_of_admission|        doctor|     hospital|insurance_provider|    billing_amount|room_number|discharge_date|medication|test_results|RandomDays|       DOB|Age|is_female|is_pediatric|sub_level_admission|  stay_type|      possible_tests|           stay_name|is_geriatric|row_num|
+-------------------+-----------+------+----------+-----------------+-----------------+--------------+-------------+------------------+------------------+-----------+--------------+----------+------------+----------+----------+---+---------+------------+-------------------+-----------+--------------

In [48]:
ranked_df.where((col("gender") == "Male") & (col("is_female") == True)).show()

+-------------------+----+------+----------+-----------------+-----------------+------+--------+------------------+--------------+-----------+--------------+----------+------------+----------+---+---+---------+------------+-------------------+---------+--------------+---------+------------+-------+
|top_level_admission|name|gender|blood_type|medical_condition|date_of_admission|doctor|hospital|insurance_provider|billing_amount|room_number|discharge_date|medication|test_results|RandomDays|DOB|Age|is_female|is_pediatric|sub_level_admission|stay_type|possible_tests|stay_name|is_geriatric|row_num|
+-------------------+----+------+----------+-----------------+-----------------+------+--------+------------------+--------------+-----------+--------------+----------+------------+----------+---+---+---------+------------+-------------------+---------+--------------+---------+------------+-------+
+-------------------+----+------+----------+-----------------+-----------------+------+--------+----

In [13]:
ranked_df.show(n=8000)

24/02/03 17:34:04 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+-------------------+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+--------------------+-----------+--------------------+------------+-------+
|top_level_admission|                name|gender|blood_type|medical_condition|date_of_admission|              doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date| medication|test_results|RandomDays|       DOB|Age|is_female|is_pediatric| sub_level_admission|  stay_type|      possible_tests|is_geriatric|row_num|
+-------------------+--------------------+------+----------+-----------------+-----------------+--------------------+--------------------+------------------+------------------+-----------+--------------+-----------+------------+----------+----------+---+---------+------------+-----------------

In [49]:
not_geriatric_df = ranked_df.where((col('sub_level_admission')== 'geriatrics') &( col("is_geriatric")== False))

ranked_tot = get_row_count(ranked_df)
geriatric_tot = get_row_count(not_geriatric_df)

filtered_df = ranked_df.join(not_geriatric_df, on= ['sub_level_admission', 'DOB'], how="left_anti")

filtered_tot = get_row_count(filtered_df)

assert filtered_tot == ranked_tot - geriatric_tot, "Row counts do not match expected value"

# checks the above calculation
assert get_row_count(filtered_df.where((col('sub_level_admission')== 'geriatrics') &( col("is_geriatric")== False))) == 0

In [17]:
# TODO filter on is pediatric, geriatric and is_female to be done here and same people with dob? needs  to be considered 

In [50]:
not_female_df = filtered_df.where((col("sub_level_admission").isin(female_only)) & (col("is_female") == False))

assert  not_female_df.where((col("gender") == "Female") & (col("is_female") == True)).count() == 0

In [53]:
not_female_tot = get_row_count(not_female_df)

filtered_df_female = filtered_df.join(not_female_df, on=['sub_level_admission', 'DOB'], how = 'left_anti')

filtered_female_tot = get_row_count(filtered_df_female, True)

assert  filtered_df_female.where((col("gender") == "Male") & (col("is_female") == True)).count() == 0

67623


In [72]:
# filter pediatric patients who cannot be pregnant (based on legal age in the UK, 16) 
under16_female_df = filtered_df_female.where((col("Age") >16) &  (col("is_female") == False)).orderBy("Age")

In [73]:
under16_female_df.show()

+-------------------+----------+-------------------+-----------------+------+----------+-----------------+-----------------+---------------+--------------------+------------------+------------------+-----------+--------------+----------+------------+----------+---+---------+------------+-----------+--------------------+--------------------+------------+-------+
|sub_level_admission|       DOB|top_level_admission|             name|gender|blood_type|medical_condition|date_of_admission|         doctor|            hospital|insurance_provider|    billing_amount|room_number|discharge_date|medication|test_results|RandomDays|Age|is_female|is_pediatric|  stay_type|      possible_tests|           stay_name|is_geriatric|row_num|
+-------------------+----------+-------------------+-----------------+------+----------+-----------------+-----------------+---------------+--------------------+------------------+------------------+-----------+--------------+----------+------------+----------+---+-------

In [54]:
# Filter to keep only the top-ranked row within each partition
ranked_df = filtered_df_female

In [55]:
ranked_df.where(col("name") == "Daniel Mccoy").show(n=8000)

+-------------------+----------+-------------------+------------+------+----------+-----------------+-----------------+-------------+-----------+------------------+------------------+-----------+--------------+----------+------------+----------+---+---------+------------+-----------+--------------------+--------------------+------------+-------+
|sub_level_admission|       DOB|top_level_admission|        name|gender|blood_type|medical_condition|date_of_admission|       doctor|   hospital|insurance_provider|    billing_amount|room_number|discharge_date|medication|test_results|RandomDays|Age|is_female|is_pediatric|  stay_type|      possible_tests|           stay_name|is_geriatric|row_num|
+-------------------+----------+-------------------+------------+------+----------+-----------------+-----------------+-------------+-----------+------------------+------------------+-----------+--------------+----------+------------+----------+---+---------+------------+-----------+--------------------

In [21]:
from pyspark.sql.types import StringType

df = filtered_df_female.select([col(c).cast(StringType()).alias(c) for c in df.columns])
df.write.csv('./temp_data/female/filtered_df_female.csv', mode = 'overwrite', header=True)

In [ ]:
        # .withColumn("top_level_admission", 
        #             when(col("is_pediatric"), 
        #                     concat(lit(ColConstants.peds), 
        #                            col("top_level_admission")
        #                            )
        #                     ).otherwise(col("top_level_admission"))
        #             )

In [ ]:
spark.stop()

In [17]:
cancer = ["Biopsy", "Blood tests", "MRI", "CT scans", "PET scans", "X-rays", "Ultrasound"]
oncology = ["Biopsies", "Blood tests", "Imaging tests (CT, MRI, PET scans)"]

In [19]:
oncology_2 = set(cancer).union(set(oncology))

In [22]:
list(oncology_2)

['Biopsies',
 'MRI',
 'Ultrasound',
 'Blood tests',
 'Imaging tests (CT, MRI, PET scans)',
 'PET scans',
 'X-rays',
 'Biopsy',
 'CT scans']